# Jitter amplification in our X-band linac from 100 to 500 MeV

In [ ]:
%plot -f SVG

In [ ]:
RF_Track;

## Load the field map from a file
This field map is inspired by the structure presented in this paper: 

W. L. Millar et al., "High-Power Test of Two Prototype X-Band Accelerating Structures Based on SwissFEL Fabrication Technology," in IEEE Transactions on Nuclear Science, vol. 70, no. 1, pp. 1-19, Jan. 2023, doi: 10.1109/TNS.2022.3230567. https://ieeexplore.ieee.org/document/9991980

In [ ]:
T = load('../data/TWS_Xband.dat');

## Prepare for the RF-Track element

In [ ]:
Ez = T(:,2) + 1j * T(:,3); % MV/m
hz = T(2,1) - T(1,1); % m

Let's plot it to see what it looks like

In [ ]:
hold on
plot(T(:,1), real(Ez))
plot(T(:,1), imag(Ez))

G_map = mean(abs(Ez)); % V/m

## Create a new element
The field map was computed assuming 37.5 MW input power to provide a 100 MV/m peak field. We want to operate this structure at an 80 MV/m peak field. In a TW structure, the power and the gradient are related by the following expression: $$G = \sqrt{\frac{\omega r/Q P}{v_g}}.$$ 

Assuming a linear relationship between the gradient $G$ and the max $E_z$ field, the required input power must be reduced according to the following expression:
$$
P_\text{actual} = P_\text{map}\left( {\frac{E_\text{z max, actual}}{E_\text{z max, map}}} \right)^2.
$$

Like in the previous example, we create a new element of type RF_FieldMap_1D, but, this time, we add two new arguments to the constructor, $ P_\text{map}$ and $P_\text{actual}$ to specify our operating input power.

In [ ]:
freq = 11.9942e9; % Hz
phid = 0; % degrees

E_map = 100e6; % V/m, the max Ez field of the field map
E_actual = 80e6; % V/m, our max Ez field 

P_map = 37.5e6; % W, the field map was generated assuming 37.5 MW input power, to provide 100 MV/m gradient
P_actual = P_map * E_actual^2/E_map^2; % W, we want to operate at 80 MV/m

RF = RF_FieldMap_1d (Ez, hz, -1, freq, +1, P_map, P_actual);
RF.set_phid (phid);
RF.set_nsteps (1000);

% OK, let's be a little faster, using a constant Ez field.

G_actual = G_map * sqrt(P_actual / P_map); % V/m, G_actual = 60.72 MV/m

RF = Drift( RF.get_length() );
RF.set_static_Efield (0, 0, -G_actual);

Let's plot the field using ```get_field()```

In [ ]:
RF.set_t0(0.0); % for plotting
T_period = RF.get_period(); % mm/c

Z = linspace(0, RF.get_length()*1e3, 1000); % mm
O = zeros(size(Z));
I = ones(size(Z));

for t = [ 0.0 0.3 0.6 ]*T_period

    % read the field
    [E,B] = RF.get_field (O, O, Z, t*I);
    figure;
    plot (Z, E(:,3) / 1e6);
    title (sprintf('t = %2.f%% of period', t*100/T_period));
    xlabel ('Z [mm]');
    ylabel ('E_z [MV/m]');
    
end

RF.unset_t0();

In [ ]:
L_RF = RF.get_length()

## Let's define some beam parameters

In [ ]:
%% Bunch parameters
mass = RF_Track.electronmass; % MeV/c^2
Q = -1; % single-particle charge, in units of e
population = 50 * RF_Track.pC; % number of real particles per bunch

P_i = 100; % initial momentum, MeV/c
P_f = 500; % final momentum, MeV/c

## Let's build the linac lattice
We use a standard FODO lattice, with four structures every two consecutive quadrupoles and 90 degrees phase advance per cell

In [ ]:
%% FODO cell parameters
Lquad = 0.1; % m
Lcell = 8*L_RF + 2*Lquad; % m, eight structures and two quadrupoles

In [ ]:
mu = 90; % deg
k1L = sind(mu/2) / (Lcell/4); % 1/m, integrateg focusing strength

### The unit FODO cell
Each FODO cell can be considered as an RF module.
Initially, we leave the quadrupoles off; their strength is 0.0.

In [ ]:
FODO = Lattice();
FODO.append ( RF );
FODO.append ( RF );
FODO.append ( RF );
FODO.append ( RF );
FODO.append ( Quadrupole (Lquad, 0.0 ));
FODO.append ( RF );
FODO.append ( RF );
FODO.append ( RF );
FODO.append ( RF );
FODO.append ( Quadrupole (Lquad, 0.0 ));

We need to find what is the maximum energy gain per cell, so we define a reference particle and track it through the cell

In [ ]:
% Define the reference particle
P0 = Bunch6d (mass, population, Q, [ 0 0 0 0 0 P_i ]);

% We use autophase to set the phases and to determine P_max, the maximum final momentum
P_max = FODO.autophase (P0); % MeV/c

% The momentum gain is
P_gain = P_max - P_i   % MeV/c

Let's compute how many FODO cells we need

In [ ]:
n_FODO = (P_f - P_i) / P_gain

In [ ]:
n_FODO = round(n_FODO)    % let's round it to the nearest integer

As we intend to use several instances of the same FODO cell, we need to unset the reference time from FODO so that we can put four cells in a lattice and have each have its own reference time.

In [ ]:
FODO.unset_t0()

% Start a new lattice
LINAC = Lattice();

% 1/2 quad, let's start with half a quad
LINAC.append ( Quadrupole (Lquad/2, 0.0) );

% let's put out n_FODO cells
for i=1:n_FODO
    LINAC.append (FODO);
end

In [ ]:
LINAC.get_length()

## Let's track the reference particle and do some plots

In [ ]:
% Track the reference particle
P1 = LINAC.track(P0);

Plot the energy profile along the linac

In [ ]:
% Extract the "transport table"
T = LINAC.get_transport_table('%S %mean_P');

plot (T(:,1), T(:,2))
xlabel ('S [m]')
ylabel ('K [MeV]')

Now, we need to set the quadrupole strengths. We can use ```set_K1```, which accepts two parameters:
* the reference rigidity, $P/q$
* the quadrupole's focusing strength, in 1/m$^2$

In [ ]:
Quads = LINAC.get_quadrupoles();

In [ ]:
length(Quads)

It is convenient to use the normalised focusing strength, $k_1$

In [ ]:
k1 = k1L / Lquad; % 1/m^2

In [ ]:
half_P_gain = 0.5 * P_gain;

P = P_i; % initial momentum
for q = Quads

  % set quadrupole strength
  q{1}.set_K1 (P/Q, k1);
 
  % update the momentum variable
  P += half_P_gain;         % 

  % changes the sign of k1, anticipating the next quadrupole
  k1 = -k1;
 
end

## Define a bunch

In [ ]:
%% Define Twiss parameters
Twiss = Bunch6d_twiss();
Twiss.emitt_x = 5; % mm.mrad, normalized emittances
Twiss.emitt_y = 5; % mm.mrad
Twiss.beta_x = Lcell * (1 - sind(mu/2)) / sind(mu); % m
Twiss.beta_y = Lcell * (1 + sind(mu/2)) / sind(mu); % m

%% Create the bunch
B0 = Bunch6d_QR (mass, population, Q, P_i, Twiss, 10000);

Let's add an offset in X of 10% of the beam size

In [ ]:
M0 = B0.get_phase_space();

sigma_X = std(M0(:,1)) % mm

M0(:,1) += 0.1 * sigma_X; % mm, add an offset in X

B0 = Bunch6d (mass, population, Q, M0);

## Perform tracking

In [ ]:
B1 = LINAC.track(B0);

Let's make some plots...

In [ ]:
M0 = B0.get_phase_space ('%x %xp %y %yp %dt %P');
M1 = B1.get_phase_space ('%x %xp %y %yp %dt %P');

figure
hold on
scatter(M0(:,1), M0(:,2))
scatter(M1(:,1), M1(:,2))
legend({'initial', 'final'});
xlabel('x [mm]');
ylabel('x'' [mrad]');

figure
hold on
scatter(M0(:,3), M0(:,4))
scatter(M1(:,3), M1(:,4))
legend({'initial', 'final'});
xlabel('y [mm]');
ylabel('y'' [mrad]');

figure
scatter(M1(:,5), M1(:,6))
xlabel('dt [mm/c]');
ylabel('P [MeV/c]');

In [ ]:
T = LINAC.get_transport_table('%S %mean_x %mean_y');

In [ ]:
hold on
plot(T(:,1), T(:,2), 'b-', 'linewidth', 2);
plot(T(:,1), T(:,3), 'r-', 'linewidth', 2);
legend('X', 'Y');
xlabel('S [m]');
ylabel('position [mm]');

In [ ]:
T = LINAC.get_transport_table('%S %emitt_x %emitt_y');

In [ ]:
hold on
plot(T(:,1), T(:,2), 'b-', 'linewidth', 2);
plot(T(:,1), T(:,3), 'r-', 'linewidth', 2);
legend('emitt_x', 'emitt_y');
xlabel('S [m]');
ylabel('norm. emitt [mm.mrad]');

In [ ]:
%RF = Drift( RF.get_length());
%RF.set_static_Efield(0, 0, -E_actual);

## Jitter amplification study
We paint an ellipse in the input phase space to evaluate the action amplification (jitter amplification)

In [ ]:
N = 10;
Angles = linspace(0, 360, N)(1:N-1)

In [ ]:
M0 = B0.get_phase_space();

sigma_X  = std(M0(:,1)); % mm
sigma_Xp = std(M0(:,2)); % mrad

N = 10;
Angles = linspace(0, 360, N)(1:N-1)

T_X = [];
T_Xp = [];
for angle = Angles

    disp([ 'angle = ' num2str(angle) ])

    Mtemp = M0;

    Mtemp(:,1) += 0.1 * cosd(angle) * sigma_X; % mm, add an offset in X
    Mtemp(:,2) += 0.1 * sind(angle) * sigma_Xp; % mrad, add an offset in X'

    Btest = Bunch6d (mass, population, Q, Mtemp);

    B1 = LINAC.track(Btest);

    T = LINAC.get_transport_table('%mean_x %mean_Px');

    T_X  = [ T_X ; T(:,1)' ];
    T_Xp = [ T_Xp ; T(:,2)' ];

end

In [ ]:
size(T_X)

In [ ]:
plot(T_X)
xlabel('S [m]')
ylabel('X [mm]')

In [ ]:
scatter(T_X(:,1), T_Xp(:,1))
xlabel('X [mm]')
ylabel('P_x [MeV/c]')
title('Offsets at linac start')

In [ ]:
scatter(T_X(:,end), T_Xp(:,end))
xlabel('X [mm]')
ylabel('P_x [MeV/c]')
title('Offsets at linac end')

In [ ]:
Ai = polyarea (T_X(:,1), T_Xp(:,1))

In [ ]:
Af = polyarea (T_X(:,end), T_Xp(:,end))

In [ ]:
Amplification_factor = Af / Ai